## Install the modified `dom-tokenizers`

In [ ]:
!git clone https://github.com/gbenson/dom-tokenizers.git -b emit-unique-tokens-0.0.18-pre1 --single-branch

Cloning into 'dom-tokenizers'...
remote: Enumerating objects: 613, done.
remote: Counting objects: 100% (187/187), done.
remote: Compressing objects: 100% (80/80), done.
remote: Total 613 (delta 118), reused 144 (delta 96), pack-reused 426
Receiving objects: 100% (613/613), 153.44 KiB | 946.00 KiB/s, done.
Resolving deltas: 100% (335/335), done.


In [ ]:
!cd dom-tokenizers && pip install -e .[train]

Obtaining file:///content/dom-tokenizers
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Preparing editable metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.5/235.5 kB 4.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.8/40.8 MB 15.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.8 MB/s eta 0:00:00
  Building editable for dom-tokenizers (pyproject.toml) ... done
  Created wheel for dom-tokenizers: filename=dom_tokenizers-0.0.18-0.editable-py3-none-any.whl size=7367 sha256=

## Train a tokenizer on `gbenson/webui-dom-snapshots`

We don't need the tokenizer, but this `dom-tokenizers` is modified to output everything [`vec64`](https://pypi.org/project/vec64/) matched into a file as a side-effect.

In [3]:
!train-tokenizer -n30000 -N4536 gbenson/webui-dom-snapshots

Output directory: /content/dom-tokenizer-30k

tokenizer_config.json: 100% 48.0/48.0 [00:00<00:00, 300kB/s]
config.json: 100% 570/570 [00:00<00:00, 2.86MB/s]
vocab.txt: 100% 232k/232k [00:00<00:00, 4.84MB/s]
tokenizer.json: 100% 466k/466k [00:00<00:00, 2.32MB/s]
Generating up to 30,000 tokens from 4,536 examples:
[00:00:01] Tokenize words                 ██████████████████ 845289   /   845289
[00:01:01] Count pairs                    ██████████████████ 845289   /   845289
[00:00:12] Compute merges                 ██████████████████ 23908    /    23908

['training', 'complete']
['token', '##izer', 'state', 'saved']
['see', 'you', 'soon', '##!', '##!']


## Merge the new tokens into the existing dataset

In [5]:
from datasets import load_dataset
old_tokens = {row["text"] for row in load_dataset("gbenson/webui-tokens-unlabelled")["train"]}
print(len(old_tokens))

1194369


In [8]:
with open("unique-tokens") as fp:
    new_tokens = {line.rstrip() for line in fp.readlines()}
print(len(new_tokens))

1446447


In [11]:
new_tokens.update(old_tokens)
print(len(new_tokens))

1616815


In [19]:
from pandas import DataFrame
df = DataFrame.from_dict({"text": list(new_tokens)})
df.head()

text
0                                             504869
1  mE7Ke2EFHY29Tk2R8kYkFqDPDfonKFMrc0EeB1dYm6jHX8...
2                                 com/books/congress
3                                          uitgaande
4                           com/dYUR98DdSwGk6zBmsIBw

In [24]:
from datasets import Dataset
dataset = Dataset.from_pandas(df)

## Upload to Hugging Face

In [25]:
dataset.push_to_hub("gbenson/webui-tokens-unlabelled")

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1617 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/1.18k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/gbenson/webui-tokens-unlabelled/commit/c22d8f38aec9d30666a8b159b12c20255fb67362', commit_message='Upload dataset', commit_description='', oid='c22d8f38aec9d30666a8b159b12c20255fb67362', pr_url=None, pr_revision=None, pr_num=None)